In [ ]:
# 네이버 기사 제목 수집을 위해 설치해야 하는 패키지
# 이게 설치되어야지 아래 코드가 작동됩니다.

!pip install selenium webdriver-manager pandas openpyxl

In [ ]:
# 본격적으로 네이버 기사 제목을 수집하는 코드

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
import pandas as pd
import time

# 크롬 드라이버 설정
options = webdriver.ChromeOptions()
options.add_argument('--headless')
options.add_argument('--no-sandbox')
options.add_argument('--disable-dev-shm-usage')

# 드라이버 초기화
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)
driver.get("https://search.naver.com/search.naver?where=news&query=%EC%BA%A0%ED%95%91&sm=tab_tmr&nso=so:r,p:from20160819to20160821,a:all&sort=0")

# 일정 시간 동안 스크롤 내리기
scroll_pause_time = 2
last_height = driver.execute_script("return document.body.scrollHeight")

titles = []

while True:
    # 스크롤 내리기
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    time.sleep(scroll_pause_time)
    
    # 새로운 높이 계산 후 비교
    new_height = driver.execute_script("return document.body.scrollHeight")
    if new_height == last_height:
        break
    last_height = new_height

    # 기사 제목 수집
    news_titles = driver.find_elements(By.CSS_SELECTOR, 'a.news_tit')
    for title in news_titles:
        titles.append(title.text)

driver.quit()

# 추출된 기사 제목을 데이터프레임으로 변환
df = pd.DataFrame(titles, columns=['Title'])

# 엑셀 파일로 저장
df.to_excel('news_titles.xlsx', index=False)

print("엑셀 파일로 저장되었습니다.")
